In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import matplotlib.pyplot as plt
import os.path as osp
import os
import json
from pprint import pprint
import imageio


In [21]:
### dataset loader
base_path = '/root/PycharmProjects/VisualGrounding'
with open(osp.join(base_path, 'datasets/flickr30k_anno/box_anno.json'), 'r') as load_f:
    box_anno = json.load(load_f)

with open(osp.join(base_path, 'datasets/flickr30k_anno/sent_anno.json'), 'r') as load_f:
    sent_anno = json.load(load_f)

import torch

vg_pred_root = '{}/datasets/flickr30k_anno/precomp_proposals_nms1e4.pth'.format(base_path)
vg_pred = torch.load(vg_pred_root)

In [22]:

def get_bbox_from_sent_anno(sent_anno=None, img_id=None, bbox_anno=None):
    st_anno = sent_anno[img_id]
    gt_boxes_anno = bbox_anno[img_id]['boxes']
    phrase_type_list = []
    phrase_id_list = []
    gt_bboxes_in_img = []
    gt_phrase_id_list = list(gt_boxes_anno.keys())
    
    for sent in st_anno:
        phrases = sent['phrases']
        for phra in phrases:
            phra_id = phra['phrase_id']
            phra_type = phra['phrase_type'][0]
            if phra_id not in phrase_id_list:
                if phra_id not in gt_phrase_id_list:
                    print('img:{}, phrase:{}, phra_type:{}'.format(img_id, phra_id, phra_type))
                    continue
                else:
                    phrase_id_list.append(phra_id)
                    phrase_type_list.append(phra_type) 
                    gt_boxes = gt_boxes_anno[phra_id]    
                    if len(gt_boxes) == 1:
                        gt_bboxes_in_img.append(gt_boxes[0])
                    else:
                        gt_boxes = np.array(gt_boxes).astype(np.float32)
                        fake_boxes = [gt_boxes[:, 0].min(), gt_boxes[:, 1].min(), gt_boxes[:, 2].max(), gt_boxes[:,3].max()]
                        gt_bboxes_in_img.append(fake_boxes)
            else:
                continue
    gt_bboxes_in_img = np.array(gt_bboxes_in_img).astype(np.float32)
    assert gt_bboxes_in_img.shape[0] == len(phrase_type_list)
    
    return gt_bboxes_in_img, phrase_type_list


In [23]:
def check_recall_flickr(sent_anno, img_list, bbox_anno, thresh=0.5, precompute=None):
    
    scene_type=["people", 'other', 'bodyparts', 'scene', 'vehicles', 'instruments', 'animals', 'None', 'clothing']
    
    gt_type_boxes = {}
    recall_type_boxes = {}
    for scene in scene_type:
        gt_type_boxes[scene] = 0
        recall_type_boxes[scene] = 0
    
    for img_id in img_list:
        ## numpy N*4, list N
        gt_boxes, phrases_type = get_bbox_from_sent_anno(sent_anno, img_id, bbox_anno)
        pre_boxes = np.array(precompute[img_id]).astype(np.float32)[:, :4] ## remove the scores
#         pre_boxes = np.array(precompute[img_id+'.jpg'].bbox.numpy()).astype(np.float32) ## remove the scores
        for scene in phrases_type:
            gt_type_boxes[scene] += 1
        
        gt_boxes = torch.FloatTensor(gt_boxes)
        pre_boxes = torch.FloatTensor(pre_boxes)
        bbox_overlap = bbox_overlaps(gt_boxes, pre_boxes) ## N*100
        bbox_overlap = bbox_overlap.numpy()
        pos_ind = np.where((bbox_overlap.max(1)>thresh))[0].tolist()
        pos_phrases = np.array(phrases_type)[pos_ind].tolist()
        for pos_phra in pos_phrases:
            recall_type_boxes[pos_phra] += 1
        
    recall_list = []
    total_num_boxes = 0
    total_recall_boxes = 0
    for scene in scene_type:
        total_num_boxes += gt_type_boxes[scene]
        total_recall_boxes += recall_type_boxes[scene]
    
    print('total_num_boxes:',total_num_boxes, 'recall_boxes:', total_recall_boxes, 'recall:', total_recall_boxes/total_num_boxes)
    print(gt_type_boxes)
    print(recall_type_boxes)

In [24]:
def bbox_overlaps(anchors, gt_boxes):
    """
    anchors: (N, 4) ndarray of float
    gt_boxes: (K, 4) ndarray of float

    overlaps: (N, K) ndarray of overlap between boxes and query_boxes
    """
    N = anchors.size(0)
    K = gt_boxes.size(0)

    gt_boxes_area = ((gt_boxes[:,2] - gt_boxes[:,0] + 1) *
                (gt_boxes[:,3] - gt_boxes[:,1] + 1)).view(1, K)

    anchors_area = ((anchors[:,2] - anchors[:,0] + 1) *
                (anchors[:,3] - anchors[:,1] + 1)).view(N, 1)

    boxes = anchors.view(N, 1, 4).expand(N, K, 4)
    query_boxes = gt_boxes.view(1, K, 4).expand(N, K, 4)

    iw = (torch.min(boxes[:,:,2], query_boxes[:,:,2]) -
        torch.max(boxes[:,:,0], query_boxes[:,:,0]) + 1)
    iw[iw < 0] = 0

    ih = (torch.min(boxes[:,:,3], query_boxes[:,:,3]) -
        torch.max(boxes[:,:,1], query_boxes[:,:,1]) + 1)
    ih[ih < 0] = 0

    ua = anchors_area + gt_boxes_area - (iw * ih)
    overlaps = iw * ih / ua

    return overlaps
    

In [31]:
img_ids = list(sent_anno.keys())
with open('/root/PycharmProjects/bottom-up-extractor/precompute_proposals/precompute_proposals_nms_1e2.json', 'r') as load_f:
    precompute_boxes = json.load(load_f)
    
check_recall_flickr(sent_anno=sent_anno, img_list=img_ids, bbox_anno=box_anno, thresh=0.5, precompute=precompute_boxes)

img:2970450682, phrase:84707, phra_type:people
img:2970450682, phrase:84704, phra_type:other
img:6322363637, phrase:0, phra_type:notvisual
img:6322363637, phrase:0, phra_type:notvisual
img:6322363637, phrase:252649, phra_type:other
img:3225880532, phrase:102560, phra_type:scene
img:2391812384, phrase:0, phra_type:notvisual
img:2391812384, phrase:46005, phra_type:scene
img:944374205, phrase:283841, phra_type:other
img:944374205, phrase:283841, phra_type:other
img:944374205, phrase:0, phra_type:notvisual
img:944374205, phrase:283841, phra_type:other
img:944374205, phrase:283842, phra_type:other
img:944374205, phrase:283842, phra_type:other
img:3220767301, phrase:102198, phra_type:other
img:24830572, phrase:0, phra_type:notvisual
img:24830572, phrase:52775, phra_type:scene
img:24830572, phrase:52773, phra_type:scene
img:24830572, phrase:52776, phra_type:other
img:5093235185, phrase:228770, phra_type:other
img:5093235185, phrase:228772, phra_type:scene
img:5093235185, phrase:228770, phra_t

img:3461583471, phrase:0, phra_type:notvisual
img:3461583471, phrase:119930, phra_type:scene
img:5374764034, phrase:0, phra_type:notvisual
img:5374764034, phrase:0, phra_type:notvisual
img:33382940, phrase:0, phra_type:notvisual
img:33382940, phrase:110715, phra_type:scene
img:33382940, phrase:110711, phra_type:scene
img:33382940, phrase:0, phra_type:notvisual
img:33382940, phrase:110711, phra_type:scene
img:33382940, phrase:110711, phra_type:scene
img:283677618, phrase:0, phra_type:notvisual
img:283677618, phrase:0, phra_type:notvisual
img:283677618, phrase:0, phra_type:notvisual
img:283677618, phrase:75813, phra_type:scene
img:3579368231, phrase:129212, phra_type:scene
img:3579368231, phrase:129212, phra_type:scene
img:779266595, phrase:275283, phra_type:other
img:779266595, phrase:275287, phra_type:scene
img:4509404105, phrase:174124, phra_type:other
img:4509404105, phrase:174127, phra_type:scene
img:4509404105, phrase:174124, phra_type:other
img:7526599338, phrase:271020, phra_type

img:7764208980, phrase:274786, phra_type:other
img:7764208980, phrase:274782, phra_type:scene
img:7764208980, phrase:274782, phra_type:scene
img:4483996189, phrase:0, phra_type:notvisual
img:4483996189, phrase:0, phra_type:notvisual
img:4483996189, phrase:0, phra_type:notvisual
img:4483996189, phrase:172198, phra_type:scene
img:4483996189, phrase:172201, phra_type:other
img:4898860007, phrase:0, phra_type:notvisual
img:4898860007, phrase:216471, phra_type:scene
img:4898860007, phrase:0, phra_type:notvisual
img:4898860007, phrase:216471, phra_type:scene
img:4898860007, phrase:216472, phra_type:scene
img:4898860007, phrase:0, phra_type:notvisual
img:4898860007, phrase:216472, phra_type:scene
img:4898860007, phrase:216470, phra_type:other
img:4898860007, phrase:216472, phra_type:scene
img:51146227, phrase:0, phra_type:notvisual
img:51146227, phrase:229192, phra_type:scene
img:51146227, phrase:0, phra_type:notvisual
img:51146227, phrase:229192, phra_type:scene
img:3957716846, phrase:149543

img:7102599087, phrase:0, phra_type:notvisual
img:6005955072, phrase:246546, phra_type:scene
img:4841930476, phrase:209674, phra_type:people
img:4841930476, phrase:209679, phra_type:scene
img:4841930476, phrase:209674, phra_type:people
img:4841930476, phrase:209680, phra_type:scene
img:4841930476, phrase:209679, phra_type:scene
img:4841930476, phrase:209682, phra_type:other
img:4841930476, phrase:209674, phra_type:people
img:3270273940, phrase:0, phra_type:notvisual
img:3270273940, phrase:105885, phra_type:other
img:1429546659, phrase:0, phra_type:notvisual
img:4760335522, phrase:0, phra_type:notvisual
img:4760335522, phrase:0, phra_type:notvisual
img:4760335522, phrase:0, phra_type:notvisual
img:4760335522, phrase:0, phra_type:notvisual
img:4760335522, phrase:199915, phra_type:other
img:4760335522, phrase:199915, phra_type:other
img:446901798, phrase:171059, phra_type:other
img:446901798, phrase:171054, phra_type:people
img:446901798, phrase:171058, phra_type:other
img:446901798, phra

img:329363857, phrase:0, phra_type:notvisual
img:329363857, phrase:107441, phra_type:scene
img:3050860568, phrase:90203, phra_type:scene
img:3676432043, phrase:0, phra_type:notvisual
img:2308339460, phrase:40626, phra_type:scene
img:325696203, phrase:0, phra_type:notvisual
img:325696203, phrase:0, phra_type:notvisual
img:325696203, phrase:104861, phra_type:scene
img:2531496753, phrase:0, phra_type:notvisual
img:4641280657, phrase:185717, phra_type:scene
img:4641280657, phrase:185717, phra_type:scene
img:4641280657, phrase:185720, phra_type:other
img:2358447641, phrase:0, phra_type:notvisual
img:2358447641, phrase:43941, phra_type:other
img:2358447641, phrase:43942, phra_type:other
img:2358447641, phrase:43942, phra_type:other
img:2358447641, phrase:43942, phra_type:other
img:7249187716, phrase:267546, phra_type:other
img:7249187716, phrase:267547, phra_type:other
img:444051472, phrase:0, phra_type:notvisual
img:444051472, phrase:168299, phra_type:scene
img:444051472, phrase:0, phra_typ

...

img:6954561740, phrase:262373, phra_type:scene
img:6954561740, phrase:262372, phra_type:other
img:6954561740, phrase:0, phra_type:notvisual
img:6954561740, phrase:0, phra_type:notvisual
img:4825611289, phrase:207669, phra_type:scene
img:4825611289, phrase:207670, phra_type:scene
img:4825611289, phrase:207669, phra_type:scene
img:6451570535, phrase:254397, phra_type:other
img:6451570535, phrase:0, phra_type:notvisual
img:6451570535, phrase:254399, phra_type:other
img:6451570535, phrase:254402, phra_type:other
img:6451570535, phrase:254400, phra_type:other
img:6451570535, phrase:254397, phra_type:other
img:6451570535, phrase:254399, phra_type:other
img:6451570535, phrase:254397, phra_type:other
img:7958174552, phrase:276963, phra_type:scene
img:7958174552, phrase:276960, phra_type:other
img:7958174552, phrase:276957, phra_type:scene
img:7958174552, phrase:276966, phra_type:other
img:7958174552, phrase:276962, phra_type:other
img:7958174552, phrase:276957, phra_type:scene
img:7958174552, 

img:3210538324, phrase:101371, phra_type:other
img:3210538324, phrase:0, phra_type:notvisual
img:3210538324, phrase:101370, phra_type:scene
img:3226411414, phrase:102613, phra_type:scene
img:3226411414, phrase:102613, phra_type:scene
img:3226411414, phrase:102613, phra_type:scene
img:3226411414, phrase:102615, phra_type:scene
img:2741380826, phrase:0, phra_type:notvisual
img:2741380826, phrase:69706, phra_type:other
img:4932786099, phrase:0, phra_type:notvisual
img:4151418242, phrase:157138, phra_type:vehicles
img:4151418242, phrase:157135, phra_type:vehicles
img:4151418242, phrase:157136, phra_type:scene
img:4151418242, phrase:157135, phra_type:vehicles
img:4151418242, phrase:157136, phra_type:scene
img:6662529701, phrase:256645, phra_type:scene
img:6662529701, phrase:256639, phra_type:scene
img:6662529701, phrase:256644, phra_type:other
img:6662529701, phrase:256639, phra_type:scene
img:6662529701, phrase:256647, phra_type:scene
img:6662529701, phrase:256639, phra_type:scene
img:6662

img:2303356248, phrase:0, phra_type:notvisual
img:2303356248, phrase:40307, phra_type:scene
img:2303356248, phrase:40308, phra_type:scene
img:4785616710, phrase:0, phra_type:notvisual
img:3091369572, phrase:92797, phra_type:scene
img:3091369572, phrase:92797, phra_type:scene
img:3091369572, phrase:92797, phra_type:scene
img:3534388678, phrase:125617, phra_type:other
img:3208271313, phrase:101213, phra_type:other
img:3208271313, phrase:0, phra_type:notvisual
img:3208271313, phrase:0, phra_type:notvisual
img:3208271313, phrase:0, phra_type:notvisual
img:3208271313, phrase:101213, phra_type:other
img:3208271313, phrase:101215, phra_type:other
img:4821810079, phrase:207117, phra_type:other
img:2803895304, phrase:0, phra_type:notvisual
img:2803895304, phrase:0, phra_type:notvisual
img:2803895304, phrase:73857, phra_type:other
img:2803895304, phrase:73850, phra_type:scene
img:2803895304, phrase:73850, phra_type:scene
img:2803895304, phrase:73850, phra_type:scene
img:1941285231, phrase:0, phr

img:3418504074, phrase:116770, phra_type:scene
img:3418504074, phrase:116770, phra_type:scene
img:3418504074, phrase:116770, phra_type:scene
img:3418504074, phrase:116770, phra_type:scene
img:3418504074, phrase:116770, phra_type:scene
img:4987509732, phrase:226363, phra_type:scene
img:3258394043, phrase:104940, phra_type:scene
img:3258394043, phrase:104939, phra_type:other
img:3258394043, phrase:104944, phra_type:other
img:3258394043, phrase:104939, phra_type:other
img:5790434381, phrase:243071, phra_type:scene
img:5790434381, phrase:243071, phra_type:other
img:5790434381, phrase:0, phra_type:notvisual
img:5790434381, phrase:243071, phra_type:other
img:5790434381, phrase:0, phra_type:notvisual
img:5790434381, phrase:243071, phra_type:other
img:3601298556, phrase:130662, phra_type:scene
img:4633788691, phrase:184820, phra_type:scene
img:4633788691, phrase:0, phra_type:notvisual
img:4633788691, phrase:184820, phra_type:scene
img:4633788691, phrase:184820, phra_type:scene
img:4633788691, 

img:38137970, phrase:143638, phra_type:scene
img:263765706, phrase:63080, phra_type:scene
img:263765706, phrase:63078, phra_type:other
img:263765706, phrase:0, phra_type:notvisual
img:263765706, phrase:63079, phra_type:other
img:263765706, phrase:63082, phra_type:scene
img:2883324329, phrase:78840, phra_type:scene
img:2883324329, phrase:78840, phra_type:scene
img:2883324329, phrase:78841, phra_type:scene
img:2883324329, phrase:78840, phra_type:scene
img:733964952, phrase:268656, phra_type:people
img:3237799755, phrase:103245, phra_type:people
img:3237799755, phrase:103247, phra_type:other
img:3237799755, phrase:103248, phra_type:bodyparts
img:3237799755, phrase:103246, phra_type:scene
img:3237799755, phrase:0, phra_type:notvisual
img:3237799755, phrase:103250, phra_type:other
img:3237799755, phrase:103248, phra_type:bodyparts
img:4232844448, phrase:0, phra_type:notvisual
img:4232844448, phrase:159809, phra_type:other
img:4486441469, phrase:0, phra_type:notvisual
img:4486441469, phrase: